In [1]:
%matplotlib inline
%config InlineBackend.figure_format = 'svg' 
import pylab as plb
import numpy as np
import scipy as sp
import flylib as flb
import group_data as gd
import plotfuncs as plf
plb.rcParams['pdf.fonttype'] = 42 #allows text in saved .pdf files to be edited in illustrator
plb.rcParams['image.interpolation'] = 'Nearest'
plb.rcParams['image.cmap'] = 'BrBG'
import h5py
demo_mode = False

In [2]:
#!rm saccade_analysis_data.hdf5 

In [3]:
if demo_mode:
    mtd = h5py.File('../05_basic_open_loop_motion/open_loop_trial_db.hdf5','r')
    sac_mtd = h5py.File('saccade_analysis_data.hdf5','r')
else:
    mtd = h5py.File('../05_basic_open_loop_motion/open_loop_trial_db.hdf5','r')
    import os
    os.remove('saccade_analysis_data.hdf5')
    sac_mtd = h5py.File('saccade_analysis_data.hdf5','a')

In [4]:
if not(demo_mode):
    ground_truth_idx = np.random.choice(np.shape(mtd['normed_signals']['Ph2'])[0],100,replace = False)
    sac_mtd.create_group('ground_truth')
    gd_mtd = sac_mtd['ground_truth']
    gd_mtd['ground_truth_idx'] = ground_truth_idx
    inspected = gd_mtd.create_group('inspected_trials')
    repnum = 0
else:
    gd_mtd = sac_mtd['ground_truth']
    ground_truth_idx = gd_mtd['ground_truth_idx']
    inspected = gd_mtd['inspected_trials']
    repnum = len(set(np.array(inspected.keys()).astype(int)).intersection(ground_truth_idx))
    print "%s out of %s trials have been annotated"%(repnum,len(np.array(ground_truth_idx)))

In [282]:
# modified from code found at https://github.com/bokeh/bokeh/issues/3776
trace_idx = gd_mtd['ground_truth_idx'][repnum]
lmr = np.array(mtd['normed_signals']['Ph2'])[trace_idx]
lmr[~np.isfinite(lmr)] = 0
xi = gd.get_xio('yaw_left')
import bokeh.models as bkmod #import CustomJS, ColumnDataSource, BoxSelectTool, PanTool,WheelZoomTool,Range1d, Rect
import bokeh.plotting as bkplot #import figure, output_notebook, show

bkplot.output_notebook()

source = bkmod.ColumnDataSource(data=dict(x=[], y=[], width=[], height=[]))

callback = bkmod.CustomJS(args=dict(source=source), code="""
        // get data source from Callback args
        var data = source.get('data');

        /// get BoxSelectTool dimensions from cb_data parameter of Callback
        var geometry = cb_data['geometry'];

        /// calculate Rect attributes
        var width = geometry['x1'] - geometry['x0'];
        var height = geometry['y1'] - geometry['y0'];
        var x = geometry['x0'] + width/2;
        var y = geometry['y0'] + height/2;

        /// update data source with new Rect attributes
        data['x'].push(x);
        data['y'].push(y);
        data['width'].push(width);
        data['height'].push(height);

        // trigger update of data source
        source.trigger('change');

        // Define a callback to capture errors on the Python side
        function callback(msg){
            console.log("Python callback returned unexpected message:", msg)
        }
        callbacks = {iopub: {output: callback}};

        // Generate a command to execute in Python
        var ranges = {x: data['x'],
                      w: data['width']}
        var range_str = JSON.stringify(ranges)
        var cmd = "%s(" + range_str + ")"

        // Execute the command on the Python kernel
        var kernel = IPython.notebook.kernel;
        kernel.execute(cmd, callbacks, {silent : false});     
    """%'print_vals')

selections = list()
saccades = None

def print_vals(ranges):
    global selections
    selections = ranges

def log_saccads(h5py_group_object):
    global selections
    try:
        tgroup = h5py_group_object.create_group(str(trace_idx))
    except ValueError:
        del(h5py_group_object[str(trace_idx)])
        tgroup = h5py_group_object.create_group(str(trace_idx))
    saccades = [{'x0':x0-w/2.0,'x1':x0+w/2.0} for x0,w in zip(selections['x'],selections['w'])]
    saccades = [np.argwhere((s['x0'] < xi) & (s['x1'] > xi)) for s in saccades]
    for i,saccade in enumerate(saccades):
        tgroup[str(i)] = saccade
    return saccades

box_select = bkmod.BoxSelectTool(callback=callback,dimensions = ['width'])
pan_tool = bkmod.PanTool(dimensions = ['width'])
zoom_tool = bkmod.WheelZoomTool(dimensions = ['width'])

TOOLS="resize,crosshair,pan,wheel_zoom,box_zoom,reset,box_select,lasso_select"

p = bkplot.figure(plot_width=800,
           plot_height=400,
           tools=[box_select,pan_tool,zoom_tool],
           title="Identify Saccades",
           x_range=bkmod.Range1d(start=xi[0], end=xi[-1]/5.0),
           y_range=bkmod.Range1d(start=np.min(lmr), end=np.max(lmr)))

rect = bkmod.Rect(x='x',
            y='y',
            width='width',
            height='height',
            fill_alpha=0.3,
            fill_color='#009933')

p.add_glyph(source, rect, selection_glyph=rect, nonselection_glyph=rect)

p.line(xi,lmr)
bkplot.show(p)

Loading BokehJS ...

In [283]:
log = log_saccads(inspected)

In [284]:
repnum += 1
print repnum

93


In [285]:
mtd.close()
sac_mtd.flush()
sac_mtd.close()

In [287]:
cp saccade_analysis_data.hdf5 saccade_analysis_data_backup.hdf5

In [288]:
ls

01_saccade_annotation.ipynb      saccade_analysis_data_backup.hdf5
02_evaluate_ground_truth.ipynb   saccade_analysis_data.hdf5
03_plot_saccade_responses.ipynb  saccade_classifier_param_search.hdf5
detected_saccades_lin.hdf5       saccade_evaluation.pdf
detected_saccades_nl.hdf5        STA_kde_bottom30.pdf
detection_approach.pdf           STA_kde_top30.pdf
fiter_settings.cpkl              STAs_desciles.pdf
saccade_analysis_copy.ipynb      STAs_extrema_rasters.pdf
